In [1]:
import pandas as pd
import os
import torch
import numpy as np
import nltk
import string
from tqdm.notebook import tqdm
import gensim.downloader as api
from sympy.utilities.iterables import multiset_permutations

In [2]:
nltk.download('punkt')

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\bavik\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


True

In [3]:
nltk.download('stopwords')

[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\bavik\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


True

In [4]:
nltk.download('wordnet')

[nltk_data] Downloading package wordnet to
[nltk_data]     C:\Users\bavik\AppData\Roaming\nltk_data...
[nltk_data]   Package wordnet is already up-to-date!


True

In [6]:
os.getcwd()

'E:\\Thesis prep\\thesis_convai'

In [3]:
data_dir = "./data/"
embed_size = 300
batch_size = 10

In [4]:
requests = pd.read_table(data_dir + "train.tsv", sep = '\t', header = 0).drop_duplicates('topic_id')
requests

topic_id                                    initial_request  \
0            1                   Tell me about Obama family tree.   
39         102                          What is Fickle Creek Farm   
84         105      Tell me about sonoma county medical services.   
120        108               Tell me about of Ralph Owen Brester.   
159        109  I'm looking for information about mayo clinic ...   
...        ...                                                ...   
9113       234       tell me about dark chocolate health benefits   
9127       238                     Tell me bio of george bush sr.   
9139       240                   Tell me more about us presidents   
9151       261     Tell me about folk remedies for a sore throat.   
9163       295                     How do you tie a Windsor knot?   

                                             topic_desc  clarification_need  \
0     Find information on President Barack Obama\'s ...                   2   
39    Find general information about Fickle Creek Fa...                   2   
84    What medical services are available in Sonoma ...                   2   
120   Find biographical information about Ralph Owen...                   1   
159   What medical services are available at the May...                   2   
...                                                 ...                 ...   
9113  What are the health benefits associated with e...                   1   
9127  Find biographies of US President George H.W. B...                   2   
9139    Find a list of the full names of US presidents.                   3   
9151  What folk remedies are there for soothing a so...                   1   
9163                     How do you tie a Windsor knot?                   1   

     facet_id                                         facet_desc question_id  \
0       F0001  Find the TIME magazine photo essay "Barack Oba...      Q00384   
39      F0014  Find general information about Fickle Creek Fa...      Q00059   
84      F0025  What medical services are available in Sonoma ...      Q00457   
120     F0037  Find biographical information about Ralph Owen...      Q00297   
159     F0040  What medical services are available at the May...      Q00256   
...       ...                                                ...         ...   
9113    F0539  What are the health benefits associated with e...      Q00430   
9127    F0552  Find biographies of US President George H.W. B...      Q00402   
9139    F0558    Find a list of the full names of US presidents.      Q00201   
9151    F0633  What folk remedies are there for soothing a so...      Q00208   
9163    F0752                     How do you tie a Windsor knot?      Q00182   

                                               question  \
0     are you interested in seeing barack obamas family   
39             are you going to purchase anything there   
84    are you interested in the human services depar...   
120   are you interested in learning more about ralp...   
159   are you interested in jobs at mayo clinic jack...   
...                                                 ...   
9113  are you interested in the different candles da...   
9127  are you interested in the 1992 presidential el...   
9139  are you interested in finding out the middle n...   
9151  are you interested in folk remedies from a spe...   
9163  are you interested in different knot tying tec...   

                                                 answer  
0                    yes am interested in obamas family  
39    i dont know yet i just want general info about...  
84    no i am looking for doctors or hospitals in so...  
120                               yes and his biography  
159   no im interested in services provided at mayo ...  
...                                                 ...  
9113  no im more interested in the health benefits o...  
9127  yes i would like to know about george bush srs...  
9139  no i am interested in the name

In [16]:
df = pd.DataFrame(requests)
init_requests = df['initial_request'].to_numpy(dtype = str)
topic_ids = df['topic_id'].to_numpy(dtype = int)
clarification_need = df['clarification_need'].to_numpy(dtype = int)
req_data = [(topic_ids[i], init_requests[i], int(clarification_need[i])) for i in range(len(init_requests))]
req_data

[(1, 'Tell me about Obama family tree.', 2),
 (102, 'What is Fickle Creek Farm', 2),
 (105, 'Tell me about sonoma county medical services.', 2),
 (108, 'Tell me about of Ralph Owen Brester.', 1),
 (109, "I'm looking for information about mayo clinic Jacksonville FL", 2),
 (11, 'How to prepare for the GMAT?', 2),
 (111, "I'd like to learn about lymphoma in dogs", 2),
 (112, 'Is Kenmore heater good', 2),
 (113, 'Tell me more about HP mini 2140', 2),
 (115, 'Tell me about the pacific northwest laboratory.', 2),
 (116, 'What is California Franchise Tax Board', 2),
 (117, 'What are specific dangers of asbestos?', 2),
 (119, 'How to write a thank you letter after an interview?', 1),
 (12, 'how to hire disc jockey', 2),
 (120, 'TV on computer', 3),
 (122, 'Tell me more about Culpeper National Cemetry', 3),
 (124, 'Tell me about Bowflex Power Pro.', 2),
 (125, 'butter and margarine', 3),
 (127, "I'm looking for information on duchess county tourism", 3),
 (129, "Tell me information about Iowa'

In [17]:
req_data = np.array(req_data)
req_data

array([['1', 'Tell me about Obama family tree.', '2'],
       ['102', 'What is Fickle Creek Farm', '2'],
       ['105', 'Tell me about sonoma county medical services.', '2'],
       ['108', 'Tell me about of Ralph Owen Brester.', '1'],
       ['109',
        "I'm looking for information about mayo clinic Jacksonville FL",
        '2'],
       ['11', 'How to prepare for the GMAT?', '2'],
       ['111', "I'd like to learn about lymphoma in dogs", '2'],
       ['112', 'Is Kenmore heater good', '2'],
       ['113', 'Tell me more about HP mini 2140', '2'],
       ['115', 'Tell me about the pacific northwest laboratory.', '2'],
       ['116', 'What is California Franchise Tax Board', '2'],
       ['117', 'What are specific dangers of asbestos?', '2'],
       ['119', 'How to write a thank you letter after an interview?',
        '1'],
       ['12', 'how to hire disc jockey', '2'],
       ['120', 'TV on computer', '3'],
       ['122', 'Tell me more about Culpeper National Cemetry', '3'],
     

In [18]:
inputs = req_data[:,1]
labels = [int(label) for label in req_data[:,2]]
topics = req_data[:,0]

In [19]:
labels

[2,
 2,
 2,
 1,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 2,
 1,
 2,
 3,
 3,
 2,
 3,
 3,
 2,
 3,
 2,
 2,
 4,
 2,
 2,
 3,
 4,
 3,
 1,
 2,
 2,
 4,
 3,
 2,
 2,
 2,
 1,
 2,
 4,
 3,
 3,
 3,
 2,
 3,
 2,
 3,
 3,
 2,
 3,
 1,
 3,
 2,
 2,
 2,
 3,
 1,
 4,
 3,
 3,
 1,
 1,
 2,
 1,
 3,
 2,
 3,
 2,
 2,
 2,
 2,
 3,
 3,
 2,
 2,
 2,
 3,
 2,
 3,
 3,
 3,
 2,
 3,
 3,
 3,
 3,
 2,
 2,
 3,
 4,
 2,
 4,
 3,
 2,
 4,
 1,
 2,
 3,
 1,
 2,
 4,
 4,
 4,
 3,
 1,
 2,
 4,
 3,
 4,
 4,
 3,
 2,
 4,
 3,
 3,
 4,
 3,
 3,
 2,
 2,
 4,
 4,
 4,
 2,
 3,
 3,
 2,
 3,
 2,
 1,
 1,
 1,
 2,
 3,
 1,
 2,
 1,
 1,
 4,
 2,
 2,
 1,
 1,
 1,
 2,
 1,
 2,
 3,
 3,
 3,
 2,
 2,
 3,
 2,
 3,
 2,
 4,
 3,
 2,
 2,
 4,
 2,
 2,
 3,
 3,
 4,
 3,
 3,
 2,
 2,
 4,
 2,
 3,
 3,
 3,
 3,
 3,
 3,
 2,
 4,
 4,
 2,
 1,
 2,
 3,
 1,
 1]

In [20]:
labels = np.array(labels)
labels.shape

(187,)

In [23]:
np.histogram(labels, bins = [1,2,3,4,5])

(array([25, 74, 62, 26], dtype=int64), array([1, 2, 3, 4, 5]))

In [12]:
inputs = np.array([req.lower() for req in inputs])
inputs = np.array([req.strip() for req in inputs])
inputs = np.array([req.translate(str.maketrans('', '', string.punctuation)) for req in inputs])
inputs = np.array([np.array(nltk.tokenize.word_tokenize(req)) for req in inputs])

In [13]:
inputs

array([array(['tell', 'me', 'about', 'obama', 'family', 'tree'], dtype='<U6'),
       array(['what', 'is', 'fickle', 'creek', 'farm'], dtype='<U6'),
       array(['tell', 'me', 'about', 'sonoma', 'county', 'medical', 'services'],
      dtype='<U8'),
       array(['tell', 'me', 'about', 'of', 'ralph', 'owen', 'brester'],
      dtype='<U7'),
       array(['im', 'looking', 'for', 'information', 'about', 'mayo', 'clinic',
       'jacksonville', 'fl'], dtype='<U12'),
       array(['how', 'to', 'prepare', 'for', 'the', 'gmat'], dtype='<U7'),
       array(['id', 'like', 'to', 'learn', 'about', 'lymphoma', 'in', 'dogs'],
      dtype='<U8'),
       array(['is', 'kenmore', 'heater', 'good'], dtype='<U7'),
       array(['tell', 'me', 'more', 'about', 'hp', 'mini', '2140'], dtype='<U5'),
       array(['tell', 'me', 'about', 'the', 'pacific', 'northwest', 'laboratory'],
      dtype='<U10'),
       array(['what', 'is', 'california', 'franchise', 'tax', 'board'],
      dtype='<U10'),
       array(['w

In [14]:
np.array(list(multiset_permutations(inputs[1])))

array([['creek', 'farm', 'fickle', 'is', 'what'],
       ['creek', 'farm', 'fickle', 'what', 'is'],
       ['creek', 'farm', 'is', 'fickle', 'what'],
       ['creek', 'farm', 'is', 'what', 'fickle'],
       ['creek', 'farm', 'what', 'fickle', 'is'],
       ['creek', 'farm', 'what', 'is', 'fickle'],
       ['creek', 'fickle', 'farm', 'is', 'what'],
       ['creek', 'fickle', 'farm', 'what', 'is'],
       ['creek', 'fickle', 'is', 'farm', 'what'],
       ['creek', 'fickle', 'is', 'what', 'farm'],
       ['creek', 'fickle', 'what', 'farm', 'is'],
       ['creek', 'fickle', 'what', 'is', 'farm'],
       ['creek', 'is', 'farm', 'fickle', 'what'],
       ['creek', 'is', 'farm', 'what', 'fickle'],
       ['creek', 'is', 'fickle', 'farm', 'what'],
       ['creek', 'is', 'fickle', 'what', 'farm'],
       ['creek', 'is', 'what', 'farm', 'fickle'],
       ['creek', 'is', 'what', 'fickle', 'farm'],
       ['creek', 'what', 'farm', 'fickle', 'is'],
       ['creek', 'what', 'farm', 'is', 'fickle'],


In [15]:
inputs_aug = []
labels_aug = []
for i in tqdm(range(len(inputs))):
    perms = list(multiset_permutations(inputs[i]))[:100]
    for p in perms:
        inputs_aug.append(np.array(p, dtype = np.str))
        labels_aug.append(labels[i])

In [16]:
inputs_aug = np.array(inputs_aug)

In [17]:
len(inputs_aug)

15716

In [14]:
stop_words = set(nltk.corpus.stopwords.words('english'))  

In [31]:
stop_words = set(nltk.corpus.stopwords.words('english'))  
filtered_req = []
embeds = []
lemmatizer = nltk.stem.WordNetLemmatizer()
for i in tqdm(range(len(inputs_aug))):
    filtered_req_words = [lemmatizer.lemmatize(w) for w in inputs_aug[i] if not w in stop_words]
    embeddings = []
    for word in filtered_req_words:
        if word in wv.vocab:
            embeddings.append(wv[word])
        else:
            embeddings.append(np.random.random(300))
    embeds.append(np.array(embeddings))
    filtered_req.append(np.array(filtered_req_words))
inputs = np.array(filtered_req)
embeds

[array([[-0.01879883, -0.11816406, -0.14355469, ..., -0.05566406,
          0.12255859, -0.10253906],
        [-0.12353516,  0.07226562,  0.171875  , ..., -0.02246094,
          0.06689453,  0.02685547],
        [-0.04125977, -0.20800781,  0.06445312, ..., -0.18457031,
          0.17871094, -0.00747681],
        [ 0.484375  ,  0.12255859, -0.15722656, ..., -0.08886719,
         -0.04296875,  0.01916504]], dtype=float32),
 array([[-0.01879883, -0.11816406, -0.14355469, ..., -0.05566406,
          0.12255859, -0.10253906],
        [-0.12353516,  0.07226562,  0.171875  , ..., -0.02246094,
          0.06689453,  0.02685547],
        [ 0.484375  ,  0.12255859, -0.15722656, ..., -0.08886719,
         -0.04296875,  0.01916504],
        [-0.04125977, -0.20800781,  0.06445312, ..., -0.18457031,
          0.17871094, -0.00747681]], dtype=float32),
 array([[-0.01879883, -0.11816406, -0.14355469, ..., -0.05566406,
          0.12255859, -0.10253906],
        [-0.04125977, -0.20800781,  0.06445312, 

In [22]:
inputs[15615]

array(['folk', 'throat', 'sore', 'tell', 'remedy'], dtype='<U6')

In [30]:
embeds

array([array(['family', 'obama', 'tell', 'tree'], dtype='<U6'),
       array(['family', 'obama', 'tree', 'tell'], dtype='<U6'),
       array(['family', 'tell', 'obama', 'tree'], dtype='<U6'), ...,
       array(['knot', 'windsor', 'tie'], dtype='<U7'),
       array(['tie', 'knot', 'windsor'], dtype='<U7'),
       array(['tie', 'windsor', 'knot'], dtype='<U7')], dtype=object)

In [26]:
embeds = np.array(inputs)
embeds.shape

(15716,)

In [27]:
len(embeds)

15716

In [28]:
max_sent_len = 0
for i in tqdm(range(len(embeds))):
    if len(embeds[i])>max_sent_len:
        max_sent_len = len(embeds[i])

max_sent_len

8

In [29]:
padder = np.zeros(embed_size)
embed_padded =  np.zeros((len(embeds),max_sent_len,300), dtype=float)

for i in tqdm(range(len(embeds))):
    pad_length = max_sent_len - len(embeds[i])
    embed_padded[i] = np.pad(embeds[i], ((0, pad_length), (0, 0)))


ValueError: operands could not be broadcast together with remapped shapes [original->remapped]: (2,2) and requested shape (1,2)

In [ ]:
embed_padded.shape

In [ ]:
embed_padded = np.expand_dims(embed_padded, axis = 3)
embed_padded.shape

In [ ]:
np.save('train_w2v_embeds.npy', embed_padded)

In [ ]:
labels = req_data[:,2]

In [ ]:
labels_aug = np.array([int(labels_aug[i]) for i in range(len(labels_aug))])
labels_aug = labels_aug - 1

In [ ]:
labels_aug

In [ ]:
np.save('labels_train_embeds.npy', labels_aug)

In [8]:
df_dev = pd.read_table(data_dir + "dev.tsv", sep = '\t').drop_duplicates('topic_id')
df_dev

topic_id                                    initial_request  \
0          101  Find me information about the Ritz Carlton Lak...   
60         106      I'm looking for universal animal cuts reviews   
102        107                 tell me about cass county missouri   
192        114                  Tell about an adobe indian house?   
231        123                    What is von Willebrand Disease?   
267        128              Tell me about atypical squamous cells   
303        133                          all men are created equal   
378        139             Tell me more about Rocky Mountain News   
426        142  Find me information about the sales tax in Ill...   
471        164        I'm looking for information on hobby stores   
539        165          I’m looking for blue throated hummingbird   
607        166    Tell me information about computer programming.   
677        169             What should I know about the civil war   
725        174                    I want to learn about rock art.   
800         18        I'm looking for a wedding budget calculator   
870        190                    Find Brooks Brothers clearance.   
915        191                      When can I see Churchil Downs   
967        193             Where should I order dog clean-up bags   
1018       195                  Where can I buy pressure washers?   
1066       200    Find information on ontario california airport.   
1142        24                            tell me about diversity   
1198        25                          Tell me more about Euclid   
1237        27                           Tell me about Starbucks.   
1322        35                        Find information on Hoboken   
1406        37                        Tell me about pampered chef   
1458        45               Give me information on solar panels.   
1488        71            Find information about living in India.   
1548        74                                 Tell me about kiwi   
1587         8                   I want to know about appraisals.   
1639        85  Find information from the milwaukee journal se...   
1695       214  What does the US capital gains tax rate consis...   
1708       219         What was the name of Elvis Presley's home?   
1720       229                     Fine me beef stroganoff recipe   
1732       250                  What are problems with ford edge?   
1745       252              Tell me about history of orcas island   
1757       262          Find more information about baldness cure   
1769       283                 Find information on hayrides in pa   
1781       287  What are treatments for carotid cavernous fist...   
1790       293  Tell me about the educational advantages of so...   
1802       110            where to go if I made a crime in Brazil   
1847       118                   What is Poem in Your Pocket Day?   
1895       126                    Find me a map of the US Capitol   
1923       152                      How to cure angular cheilitis   
1975        20                             Tell me about defender   
2035        44                                 Find me map of USA   
2120        51                    Tell me more about horse hooves   
2195        79                              tell me about Voyager   
2251        83                               tell me about memory   
2293       256         Who is the patron saint of mental illness?   
2305       292  i'm interested in history of the electronic me...   

                                             topic_desc  clarification_need  \
0     Find information about the Ritz Carlton resort...                   2   
60    Find testimonials of Universal Animal Cuts nut...                   3   
102   Find demographic information about Cass County...                   3   
192                  How does one build an adobe house?                   2   
231                     What is von Willebrand Disease?                   3   
267   What d

In [9]:
init_requests_dev = df_dev['initial_request'].to_numpy(dtype = str)
topic_ids_dev = df_dev['topic_id'].to_numpy(dtype = int)
clarification_need_dev = df_dev['clarification_need'].to_numpy(dtype = int)
req_data_dev = [(topic_ids_dev[i], init_requests_dev[i], clarification_need_dev[i]) for i in range(len(init_requests_dev))]
len(req_data_dev)

50

In [10]:
req_data_dev = np.array(req_data_dev)
len(req_data_dev)

50

In [11]:
inputs_dev = req_data_dev[:,1]
labels_dev = req_data_dev[:,2]
topics_dev = req_data_dev[:,0]

In [12]:
inputs_dev = np.array([req.lower() for req in inputs_dev])
inputs_dev = np.array([req.strip() for req in inputs_dev])
inputs_dev = np.array([req.translate(str.maketrans('', '', string.punctuation)) for req in inputs_dev])
inputs_dev = np.array([np.array(nltk.tokenize.word_tokenize(req)) for req in inputs_dev])

In [15]:
filtered_req_dev = []
embeds_dev = []
for i in tqdm(range(len(inputs_dev))):
    filtered_req_words = [lemmatizer.lemmatize(w) for w in inputs_dev[i] if not w in stop_words]
    embeddings = []
    for word in filtered_req_words:
        if word in wv.vocab:
            embeddings.append(wv[word])
        else:
            embeddings.append(np.random.random(300))
    embeds_dev.append(np.array(embeddings))
    filtered_req_dev.append(np.array(filtered_req_words))
inputs_dev = np.array(filtered_req)
inputs_dev

NameError: name 'lemmatizer' is not defined

In [ ]:
embeds_dev = np.array(embeds_dev)
embeds_dev.shape

In [ ]:
req_data_dev.shape

In [ ]:
max_sent_len_dev = 0
for i in tqdm(range(len(embeds_dev))):
    if len(embeds_dev[i])>max_sent_len_dev:
        max_sent_len_dev = len(embeds_dev[i])

max_sent_len_dev

In [ ]:
embeds_dev

In [ ]:
embed_padded_dev =  np.zeros((len(embeds_dev),7,300), dtype=float)

for i in tqdm(range(len(embeds_dev))):
    pad_length = max_sent_len_dev - len(embeds_dev[i])
    embed_padded_dev[i] = np.pad(embeds_dev[i], ((0, pad_length), (0, 0)))


In [ ]:
np.save('dev_w2v_embeds.npy', embed_padded_dev)

In [ ]:
len(embed_padded_dev)

In [ ]:
len(topics_dev)

In [ ]:
np.save('topics_dev.npy', topics_dev)

In [16]:
labels_dev = req_data_dev[:,2]

In [17]:
labels_dev

array(['2', '3', '3', '2', '3', '2', '2', '2', '2', '4', '3', '3', '4',
       '4', '2', '2', '2', '3', '2', '3', '4', '4', '3', '3', '3', '2',
       '3', '3', '4', '3', '1', '1', '1', '2', '2', '2', '2', '2', '2',
       '3', '2', '2', '3', '4', '2', '2', '4', '4', '1', '3'],
      dtype='<U77')

In [18]:
labels_dev = np.array([int(labels_dev[i]) for i in range(len(labels_dev))])
labels_dev = labels_dev

In [19]:
labels_dev.shape

(50,)

In [20]:
np.save('labels_dev_embeds.npy', labels_dev)

In [ ]:
labels_final = np.concatenate((labels, labels_dev))

In [ ]:
labels_final.shape

In [ ]:
embed_padded_dev

In [ ]:
embed_padded_dev = np.expand_dims(embed_padded_dev, axis = 3)
embed_padded_dev.shape

In [ ]:
embeds_final = np.concatenate((embed_padded, embed_padded_dev))

In [ ]:
embeds_final.shape

In [ ]:
np.save('training_embeds_w2v.npy', embeds_final)

In [ ]:
np.save('training_labels_w2v.npy', labels_final)

In [ ]:
requests_test = pd.read_table(data_dir + "test.tsv", sep = '\t', header = 0)
requests_test

In [ ]:
df_test = pd.DataFrame(requests_test)
init_requests_test = df_test['initial request'].to_numpy(dtype = str)
topic_ids_test = df_test['topic_id'].to_numpy(dtype = int)
req_data_test = [(topic_ids_test[i], init_requests_test[i]) for i in range(len(init_requests_test))]

In [ ]:
req_data_test = set(req_data_test)
req_data_test = np.array(list(req_data_test))
req_data_test

In [ ]:
inputs_test = req_data_test[:,1]
topics_test = req_data_test[:,0]

In [ ]:
inputs_test = np.array([req.lower() for req in inputs_test])
inputs_test = np.array([req.strip() for req in inputs_test])
inputs_test = np.array([req.translate(str.maketrans('', '', string.punctuation)) for req in inputs_test])
inputs_test = np.array([np.array(nltk.tokenize.word_tokenize(req)) for req in inputs_test])

In [ ]:
stop_words = set(nltk.corpus.stopwords.words('english'))  
filtered_req_test = []
embeds_test = []
lemmatizer = nltk.stem.WordNetLemmatizer()
for i in tqdm(range(len(inputs_test))):
    filtered_req_words = [lemmatizer.lemmatize(w) for w in inputs_test[i] if not w in stop_words]
    embeddings = []
    for word in filtered_req_words:
        if word in wv.vocab:
            embeddings.append(wv[word])
        else:
            embeddings.append(np.random.random(300))
    embeds_test.append(np.array(embeddings))
    filtered_req_test.append(np.array(filtered_req_words))
inputs_test = np.array(filtered_req_test)
inputs_test

In [ ]:
embeds_test = np.array(embeds_test)
embeds_test

In [ ]:
inputs_test.shape

In [ ]:
max_sent_len_test = 0
for i in tqdm(range(len(embeds_test))):
    if len(embeds_test[i])>max_sent_len_test:
        max_sent_len_test = len(embeds_test[i])

max_sent_len_test

In [ ]:
embed_padded_test =  np.zeros((len(inputs_test),7,300), dtype=float)

for i in tqdm(range(len(embeds_test))):
    pad_length = max_sent_len_test  - len(embeds_test[i])
    embed_padded_test[i] = np.pad(embeds_test[i], ((0, pad_length), (0, 0)))

In [ ]:
embed_padded_test.shape

In [ ]:
topics_test

In [ ]:
np.save('test_labels.npy', topics_test)

In [ ]:
np.save('test_embeds_w2v.npy', embed_padded_test)

In [ ]:
pd.read_csv(label_file_path, sep='\t').drop_duplicates('topic_id').set_index('topic_id')[
            'clarification_need']

In [ ]:
run_dict = pd.read_csv('preds_dev_w2v.txt', sep=' ', header=None).set_index(0)[1]

In [ ]:
run_dict

In [ ]:
pd.read_csv('./data/dev.tsv', sep='\t').drop_duplicates('topic_id').set_index('topic_id')

In [ ]:
clarification_labels_dict

In [ ]:
len(run_dict)

In [ ]:
len(clarification_labels_dict)

In [ ]:
df = pd.read_csv('./data/dev.tsv', sep='\t').drop_duplicates('topic_id')

In [ ]:
tp = df['topic_id'].to_numpy()

In [ ]:
len(tp)

In [ ]:
from itertools import permutations
import numpy as np
a = np.array([1,2,3,4,5])
p = list(permutations(a))
p